### Rajath Chikkatur Srinivasa
### 002552425

In [ ]:
# importing necesary modules
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.metrics.pairwise import linear_kernel
from sklearn.datasets import fetch_20newsgroups
from collections import Counter, defaultdict
import numpy as np
import random
import os
import glob
import nltk
from nltk.corpus import reuters
from nltk import bigrams, trigrams
nltk.download('reuters')
nltk.download('punkt')

[nltk_data] Downloading package reuters to /root/nltk_data...
[nltk_data]   Package reuters is already up-to-date!
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

* Q1 Create a cosine similarity matrix for all of Shakespeare’s works found in the provided
file. This will result in a 42 by 42 matrix with the cosine similarity between each of his
works. In other words, calculate the document-wise cosine similarity between all of
Shakepeare’s works. (50 points). Use TF_IDF for this. Note, you can use the Cosine
Similarity function on scikit-learn or implement your own, but no other library/package is
allowed.

In [ ]:
folder_path = '/content/sample_data/shakespeares-works_TXT_FolgerShakespeare/'
file_content_corpus = []
filenames = []
for i in os.listdir(folder_path):
  if not i.startswith('.'):
    filenames.append(i)
    file_content = open(os.path.join(folder_path,i), 'r').read()
    file_content_corpus.append(file_content)

In [ ]:
vec = TfidfVectorizer()
X = vec.fit_transform(file_content_corpus)
cos_s = cosine_similarity(X, X)
print(cos_s)

[[1.         0.59813572 0.65459176 ... 0.52515851 0.57395169 0.69694474]
 [0.59813572 1.         0.66801609 ... 0.5890345  0.59258345 0.71771293]
 [0.65459176 0.66801609 1.         ... 0.59895863 0.66716633 0.79038899]
 ...
 [0.52515851 0.5890345  0.59895863 ... 1.         0.52277672 0.62033426]
 [0.57395169 0.59258345 0.66716633 ... 0.52277672 1.         0.70530628]
 [0.69694474 0.71771293 0.79038899 ... 0.62033426 0.70530628 1.        ]]


* Q2. Write a function that takes the previous matrix and a number n as parameters (nothing
else will be accepted) and return the top n similar works. Use the function to output the
top 10 similar works. (30 points).

In [ ]:
def top_n_similar_works(cos_matrix, n):
  topNSimilar = []
  np.fill_diagonal(cos_matrix, 0)
  index_1d = cos_matrix.flatten().argsort()[-(2*n):]
  x_idx, y_idx = np.unravel_index(index_1d, cos_matrix.shape)
  # print(x_idx)
  for i in range(0,len(x_idx),2):
    # print(x_idx[i])
    x = x_idx[i]
    y = y_idx[i]
    if(x != y):
      topNSimilar.append((x,y,cos_matrix[x][y]))
  return topNSimilar[::-1]

In [ ]:
# print(top_n_similar_works(cos_s,10))
print('top ten similar works\n')
for i in top_n_similar_works(cos_s,10):
  print(filenames[i[0]], 'is similar to', filenames[i[1]])

top ten similar works

lucrece_TXT_FolgerShakespeare.txt is similar to venus-and-adonis_TXT_FolgerShakespeare.txt
henry-iv-part-1_TXT_FolgerShakespeare.txt is similar to henry-iv-part-2_TXT_FolgerShakespeare.txt
lucrece_TXT_FolgerShakespeare.txt is similar to shakespeares-sonnets_TXT_FolgerShakespeare.txt
henry-vi-part-1_TXT_FolgerShakespeare.txt is similar to henry-vi-part-2_TXT_FolgerShakespeare.txt
richard-iii_TXT_FolgerShakespeare.txt is similar to richard-ii_TXT_FolgerShakespeare.txt
shakespeares-sonnets_TXT_FolgerShakespeare.txt is similar to venus-and-adonis_TXT_FolgerShakespeare.txt
henry-v_TXT_FolgerShakespeare.txt is similar to henry-viii_TXT_FolgerShakespeare.txt
henry-vi-part-2_TXT_FolgerShakespeare.txt is similar to henry-vi-part-3_TXT_FolgerShakespeare.txt
richard-ii_TXT_FolgerShakespeare.txt is similar to henry-vi-part-2_TXT_FolgerShakespeare.txt
henry-v_TXT_FolgerShakespeare.txt is similar to king-john_TXT_FolgerShakespeare.txt


In [ ]:
print(top_n_similar_works(cos_s,10))

[(32, 12, 0.9175430138884021), (2, 16, 0.9076165568984123), (32, 18, 0.8677688748875242), (6, 24, 0.8437915980298416), (36, 35, 0.8389525010107527), (18, 12, 0.8381452108269781), (5, 41, 0.8363042342905285), (24, 38, 0.8354926670186541), (35, 24, 0.8343507770652858), (5, 3, 0.8342954531999516)]


* Q3. Using the code from the Language Models II class, train two simple language models
using all of the files (together) in shakespeares-works_TXT_FolgerShakespeare.zip. One
model should be trained using bigrams, the other using trigrams. (40 points).

* bigrams

In [ ]:
wordtokens = []
for i in file_content_corpus:
  wordtokens.append(nltk.word_tokenize(i))

# Create a placeholder for model
bigrammodel = defaultdict(lambda: defaultdict(lambda: 0))

# Count frequency of co-occurence  
for sentence in wordtokens:
    for w1, w2 in bigrams(sentence, pad_right=True, pad_left=True):
        bigrammodel[w1][w2] += 1
 
# Let's transform the counts to probabilities
for i in bigrammodel:
    total_count = float(sum(bigrammodel[i].values()))
    for j in bigrammodel[i]:
        bigrammodel[i][j] /= total_count


In [ ]:
dict(bigrammodel["fight"])

{'!': 0.028070175438596492,
 "'gainst": 0.0035087719298245615,
 ',': 0.17192982456140352,
 '--': 0.007017543859649123,
 '.': 0.19649122807017544,
 ':': 0.0035087719298245615,
 ';': 0.017543859649122806,
 '?': 0.007017543859649123,
 'Against': 0.021052631578947368,
 'And': 0.010526315789473684,
 'Be': 0.0035087719298245615,
 'Betwixt': 0.0035087719298245615,
 'But': 0.0035087719298245615,
 'I': 0.007017543859649123,
 'In': 0.0035087719298245615,
 'Of': 0.007017543859649123,
 'This': 0.0035087719298245615,
 'To': 0.007017543859649123,
 'When': 0.007017543859649123,
 'With': 0.007017543859649123,
 'Within': 0.0035087719298245615,
 'Without': 0.0035087719298245615,
 'a': 0.0035087719298245615,
 'about': 0.0035087719298245615,
 'abroad': 0.0035087719298245615,
 'again': 0.010526315789473684,
 'against': 0.031578947368421054,
 'and': 0.017543859649122806,
 'aside': 0.0035087719298245615,
 'at': 0.010526315789473684,
 'bare-armed': 0.0035087719298245615,
 'be': 0.0035087719298245615,
 'began'

* trigrams


In [ ]:
# Create a placeholder for model
trigrammodel = defaultdict(lambda: defaultdict(lambda: 0))

# Count frequency of co-occurence  
for sentence in wordtokens:
    for w1, w2, w3 in trigrams(sentence, pad_right=True, pad_left=True):
        trigrammodel[(w1, w2)][w3] += 1
 
# Let's transform the counts to probabilities
for w1_w2 in trigrammodel:
    total_count = float(sum(trigrammodel[w1_w2].values()))
    for w3 in trigrammodel[w1_w2]:
        trigrammodel[w1_w2][w3] /= total_count
dict(trigrammodel["men", "fight"])

{'now': 1.0}

* Q4. Write a function that takes the following three parameters: model, list of start words,
number of sentences to generate. This function should return the sentences generated
as a list. DO NOT print anything to the screen from within the function. Use this function
to generate 10 sentences with the bigram model from the previous question, and 5
sentences with the trigram model from the previous question. (30 points)

In [ ]:
def function(model,start_words,num_sentences):
  sentences = []
  
  for key in model.keys():
    break
  
  if(type(key) == tuple):
    for i in range(num_sentences):
      text = start_words
      sentence_finished = False

      while not sentence_finished:
        # select a random probability threshold  
        r = random.random()
        accumulator = .0

        for word in model[tuple(text[-2:])].keys():
            accumulator += model[tuple(text[-2:])][word]
            # select words that are above the probability threshold
            if accumulator >= r:
                text.append(word)
                break

        if text[-2:] == [None, None]:
            sentence_finished = True
        
      sentences.append(' '.join([t for t in text if t]))
  else:
    for i in range(num_sentences):
      text = start_words
      sentence_finished = False

      while not sentence_finished:
        # select a random probability threshold  
        r = random.random()
        accumulator = .0

        for word in model[text[-1]].keys():
            accumulator += model[text[-1]][word]
            # select words that are above the probability threshold
            if accumulator >= r:
                text.append(word)
                break

        if text[-1:] == [None]:
            sentence_finished = True
        
      sentences.append(' '.join([t for t in text if t]))

  return sentences

In [ ]:
function(bigrammodel,["Sword"],10), function(trigrammodel,["men", "fight"],5)

(["Sword , to correct himself to the point charge ? Think'st thou dost stand upon it me weaponed . Many receipts he , and safer triumph , frighted with woe and all adventures , and other places , my fortunes . [ All you the Play , [ presenting young Shall enter fighting That did you are most joyful tongue sound -- Sirs , a little scene I am thy teeth , I , restrained , [ to retire to know it . You are too dear boy hath reference freely . [ He is this : For me but I shall try . Souls ' approve him laughing , all-noble Theseus , Where ? HAMLET No , and wail but if they come to take a king tempt , as Charles is safe , yet I say , Against my silver beard . You were forewarned . '' His face , only not like the mere word more equal men nor Hereford that his money . Go with determined he was it true or I see thy devotion , complexion of men When I 'll answer , for the grooms with him on fire fear -- the very wound my heart cool us good ones suffer with craft , if reading of pomp to woo anothe

Bonus (20 points): Using the same methodology from questions 1 and 2, create a
similarity matrix between the 20 newsgroups corpus. And find the top 5 similar
newsgroups.

In [ ]:
newsgroup = fetch_20newsgroups()
vec = TfidfVectorizer()
X = vec.fit_transform(newsgroup.data)
cos_sb = cosine_similarity(X, X)

In [ ]:
print(cos_sb)

[[1.         0.04405974 0.11017033 ... 0.04433678 0.04457107 0.0329325 ]
 [0.04405974 1.         0.06242113 ... 0.07373268 0.06959306 0.02439956]
 [0.11017033 0.06242113 1.         ... 0.07569182 0.06214891 0.02357985]
 ...
 [0.04433678 0.07373268 0.07569182 ... 1.         0.02909961 0.00716986]
 [0.04457107 0.06959306 0.06214891 ... 0.02909961 1.         0.02428174]
 [0.0329325  0.02439956 0.02357985 ... 0.00716986 0.02428174 1.        ]]


In [ ]:
print(top_n_similar_works(cos_sb,5))

[(2002, 10777, 1.0000000000000002), (14, 5392, 1.0000000000000002), (800, 9989, 1.0), (4772, 4495, 0.9997809868890166), (4772, 8665, 0.9996809512865921)]


In [ ]:
abc = top_n_similar_works(cos_sb,5)

In [ ]:
print('top 5 related news groups present in fetch_20newsgroups are:')
for i in abc:
  print(i[0])

top 5 related news groups present in fetch_20newsgroups are:
2002
14
800
4772
4772
